## Generators

In [50]:
numbers = [2,3,5,7,11]
thing = (x ** 2 for x in numbers if x % 2 != 0)

<generator object <genexpr> at 0x10b3f5700>

In [51]:
tuple(x ** 2 for x in numbers if x % 2 != 0)

(9, 25, 49, 121)

## Iterators

In [3]:
my_list = [2,3,5,7,11]

[2, 3, 5, 7, 11]

In [4]:
it = iter(my_list)

In [5]:
first = next(it)
print("First element of list:", first)

First element of list: 2


In [6]:
it = iter(my_list)
it2 = iter(my_list)

In [7]:
next(it)

2

In [8]:
next(it2)

2

In [9]:
next(it)

3

In [10]:
next(it)

5

In [11]:
next(it)

7

In [12]:
next(it)

11

In [13]:
next(it)

StopIteration: 

In [15]:
for d in my_list:
    print(d)

2
3
5
7
11


In [16]:
it = iter(my_list)
next(it)
for d in it:
    print(d)

3
5
7
11


In [17]:
for i in 7823:
    print(i)

TypeError: 'int' object is not iterable

### Generators and Lazy Evaluation

In [43]:
def square(it):
    for i in it:
        print("SQUARING", i)
        yield i*i
        
for j in square([1,2,3,4,5]):
    time.sleep(1)
    if j >= 9:
        break

SQUARING 1
SQUARING 2
SQUARING 3


In [19]:
def square2(d):
    print("SQUARING", d)
    return d * d

for j in [square2(i) for i in [1,2,3,4,5]]:
    if j >= 9:
        break

SQUARING 1
SQUARING 2
SQUARING 3
SQUARING 4
SQUARING 5


In [ ]:
def square2(d):
    print("SQUARING", d)
    return d * d

for j in (square2(i) for i in [1,2,3,4,5]):
    if j >= 9:
        break

In [21]:
for j in (square2(i) for i in [1,2,3,4,5]):
    if j >= 9:
        break

SQUARING 1
SQUARING 2
SQUARING 3


## Lazy & Eager Evaluation (+Memoization)

In [22]:
import time

def compute_fast_function(s, t):
    print("RUNNING FAST")
    return s * t
def compute_slow_function(s, t):
    print("RUNNING SLOW")
    time.sleep(2) # pause execution for 2 seconds
    return s * t

In [23]:
%%time
s = 12
t = 10
u = compute_fast_function(s, t)
v = compute_slow_function(s, t)
if s > t and s**2 + t**2 > 100:
    res = u / 100
else:
    res = v / 100
res

RUNNING FAST
RUNNING SLOW
CPU times: user 1.55 ms, sys: 1.13 ms, total: 2.68 ms
Wall time: 2 s


1.2

In [24]:
%%time
s = 12
t = 10
if s > t and s**2 + t**2 > 100:
    u = compute_fast_function(s, t)
    res = u / 100
else:
    v = compute_slow_function(s, t)
    res = v / 100
res

RUNNING FAST
CPU times: user 410 µs, sys: 363 µs, total: 773 µs
Wall time: 492 µs


1.2

In [25]:
%%time
def my_function(s, t, u, v):
    if s > t and s**2 + t**2 > 100:
        res = u / 100
    else:
        res = v / 100
    return res

s = 12
t = 10
my_function(s, t, compute_fast_function(s, t), compute_slow_function(s, t))

RUNNING FAST
RUNNING SLOW
CPU times: user 1.47 ms, sys: 1.12 ms, total: 2.59 ms
Wall time: 2 s


1.2

In [26]:
%%time
s = 10
t = 12
if s > t and compute_slow_function(s, t) > 50:
    c = compute_slow_function(s, t)
else:
    c = compute_fast_function(s, t)

RUNNING FAST
CPU times: user 344 µs, sys: 158 µs, total: 502 µs
Wall time: 453 µs


In [27]:
%%time
s = 5
t = 4
if s > t and compute_slow_function(s, t) > 50:
    c = compute_slow_function(s, t)
else:
    c = compute_fast_function(s, t)

RUNNING SLOW
RUNNING FAST
CPU times: user 1.51 ms, sys: 1.13 ms, total: 2.64 ms
Wall time: 2 s


In [28]:
%%time
s = 12
t = 10
if s > t and compute_slow_function(s, t) > 50:
    c = compute_slow_function(s, t)
else:
    c = compute_fast_function(s, t)

RUNNING SLOW
RUNNING SLOW
CPU times: user 2.31 ms, sys: 1.68 ms, total: 3.99 ms
Wall time: 4.01 s


In [31]:
%%time
s = 12
t = 10
if s > t and (c := compute_slow_function(s, t) > 50):
    pass
else:
    c = compute_fast_function(s, t)

RUNNING SLOW
CPU times: user 1.37 ms, sys: 1.12 ms, total: 2.48 ms
Wall time: 2 s


In [32]:
%%time
s = 5
t = 4
if s > t and (c := compute_slow_function(s, t) > 50):
    pass
else:
    c = compute_fast_function(s, t)

RUNNING SLOW
RUNNING FAST
CPU times: user 1.68 ms, sys: 1.28 ms, total: 2.95 ms
Wall time: 2 s


In [33]:
%%time
for s, t in [(12, 10), (4, 5), (5, 4), (12, 10)]:
    if s > t and (c := compute_slow_function(s, t) > 50):
        pass
    else:
        c = compute_fast_function(s, t)

RUNNING SLOW
RUNNING FAST
RUNNING SLOW
RUNNING FAST
RUNNING SLOW
CPU times: user 3.27 ms, sys: 1.58 ms, total: 4.84 ms
Wall time: 6.01 s


In [34]:
memo_dict = {}
def memoized_slow_function(s, t):
    if (s, t) not in memo_dict:
        print("NOT MEMOIZED")
        memo_dict[(s, t)] = compute_slow_function(s, t)
    else:
        print("MEMOIZED")
    return memo_dict[(s, t)]

In [35]:
%%time
for s, t in [(12, 10), (4, 5), (5, 4), (12, 10)]:
    if s > t and (c := memoized_slow_function(s, t) > 50):
        pass
    else:
        c = compute_fast_function(s, t)

NOT MEMOIZED
RUNNING SLOW
RUNNING FAST
NOT MEMOIZED
RUNNING SLOW
RUNNING FAST
MEMOIZED
CPU times: user 2.77 ms, sys: 2.33 ms, total: 5.11 ms
Wall time: 4.01 s


## Functional Programming

In [44]:
def upper(s):
    return s.upper()
map(upper, ['sentence', 'fragment']) # generator

In [45]:
list(map(upper, ['sentence', 'fragment']))

['SENTENCE', 'FRAGMENT']

In [46]:
def upper(s):
    return s.upper()
output = map(upper, ['sentence', 'fragment']) # generator
for d in output:
    print(d)

SENTENCE
FRAGMENT


In [47]:
def upper(s):
    return s.upper()
output = map(upper, ['sentence', 'fragment']) # generator
for d in output:
    print(d)
    if d == "SENTENCE":
        break

SENTENCE


In [48]:
[upper(s) for s in ['sentence', 'fragment']] # comprehension

['SENTENCE', 'FRAGMENT']

In [49]:
# lambda function
list(map(lambda s: s.upper(), ['sentence','fragment']))

['SENTENCE', 'FRAGMENT']

## Characters to Numbers and Back

In [36]:
ord('c') # character to int

99

In [37]:
chr(99)

'c'

In [38]:
ord('é')

233

In [39]:
hex(233)

'0xe9'

In [40]:
'\u00e9'

'é'

In [41]:
ord('😂')

128514

In [42]:
chr(128514)

'😂'